In [1]:
# created on Dec 24, 2020
# @author:          Bo Zhao
# @email:           zhaobo@uw.edu
# @website:         https://hgis.uw.edu
# @organization:    Department of Geography, University of Washington, Seattle
# @description:     Search geo-tagged tweets within the U.S. This script is modified from https://github.com/shawn-terryah/Twitter_Geolocation

!python -m pip install tweepy
import tweepy, json, time

In [2]:
class StreamListener(tweepy.StreamListener):
    """tweepy.StreamListener is a class provided by tweepy used to access
    the Twitter Streaming API to collect tweets in real-time.
    """

    def __init__(self, time_limit=60, file=""):
        """class initialization"""
        self.start_time = time.time()
        self.limit = time_limit
        self.f = open(file, 'a', encoding="utf-8")
        super(StreamListener, self).__init__()

    def on_data(self, data):
        """This is called when data are streamed in."""
        if (time.time() - self.start_time) < self.limit:
            datajson = json.loads(data)
            print(datajson, "\n")
            if 'id' not in datajson.keys():
                time.sleep(10)
            else:
                # {'limit': {'track': 13, 'timestamp_ms': '1585851016736'}}

                id = datajson['id']
                username = datajson['user']['screen_name']
                created_at = datajson['created_at']
                text = datajson['text'].strip().replace("\n", "")

                # process the geo-tags
                if datajson['coordinates'] == None:
                    try:
                        bbox = datajson['place']['bounding_box']['coordinates'][0]
                        lng = (bbox[0][0] + bbox[2][0]) / 2.0
                        lat = (bbox[0][1] + bbox[1][1]) / 2.0
                    except:
                        lat = 0
                        lng = 0
                else:
                    lng = datajson['coordinates']['coordinates'][0]
                    lat = datajson['coordinates']['coordinates'][1]

                if lat != 0:
                    record = '%s, %s, %f, %f, %s \n' % (username, created_at, lng, lat, text)
                    print(record)
                    self.f.write(record)
                else:
                    pass
        else:
            self.f.close()
            print("finished")
            return False

In [3]:
if __name__ == "__main__":
    # These are provided to you through the Twitter API after you create a account
    # register a Twitter App to get the keys and access tokens.
    output_file = "assets/tweets.csv"

    # Apply for your own Twitter API keys at https://developer.twitter.com/en/apply-for-access
    consumer_key = "NIBYcD8sodFqYDhNYLcDaSGIk"
    consumer_secret = "SAaOKexcdZZMpPlWzo3VTfDUcLNKM6HsyaBbAz5lG6P9nB1EMk"
    access_token = "891117867176910849-fnqTHjoAdm9xrH7N9MxhWwcgDZXDslI"
    access_token_secret = "4SscuKyaaqUHf0l4U03tOJoTgqR6utK4AvV575VG2vqHG"

    myauth = tweepy.OAuthHandler(consumer_key, consumer_secret)
    myauth.set_access_token(access_token, access_token_secret)

    # LOCATIONS are the longitude, latitude coordinate corners for a box that restricts the
    # geographic area from which you will stream tweets. The first two define the southwest
    # corner of the box and the second two define the northeast corner of the box.
    LOCATIONS = [-124.7771694, 24.520833, -66.947028, 49.384472,  # Contiguous US
                 -164.639405, 58.806859, -144.152365, 71.76871,  # Alaska
                 -160.161542, 18.776344, -154.641396, 22.878623]  # Hawaii

    stream_listener = StreamListener(time_limit=60, file=output_file)
    stream = tweepy.Stream(auth=myauth, listener=stream_listener)
    stream.filter(locations=LOCATIONS)
    stream.filter(track=['Nintendo'], is_async=True)

{'created_at': 'Fri Apr 24 03:08:32 +0000 2020', 'id': 1253521178293088256, 'id_str': '1253521178293088256', 'text': '🥺🥺🥺', 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 757236368347172865, 'id_str': '757236368347172865', 'name': 'Crumbbss🍪', 'screen_name': 'crumbbss_', 'location': 'Houston, TX', 'url': None, 'description': 'You niggas pussy 😭', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 339, 'friends_count': 519, 'listed_count': 1, 'favourites_count': 16156, 'statuses_count': 9690, 'created_at': 'Sun Jul 24 15:29:53 +0000 2016', 'utc_offset': None, 'time_zone': None, 'geo_enabled': True, 'lang': None, 'contributors_enabled': False, 'is_translator': False, 'profile_background_color': 'F5F8FA', 'profile_

{'created_at': 'Fri Apr 24 03:08:33 +0000 2020', 'id': 1253521179370913794, 'id_str': '1253521179370913794', 'text': 'My health insurance will not cover a flashlight enema.', 'source': '<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 442321180, 'id_str': '442321180', 'name': 'Wayne Belcher', 'screen_name': 'WayneBelcher1', 'location': 'Henderson, NV', 'url': None, 'description': 'Farm boy, Eagle Scout, hydrogeologist', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 53, 'friends_count': 171, 'listed_count': 0, 'favourites_count': 1305, 'statuses_count': 2329, 'created_at': 'Wed Dec 21 00:32:04 +0000 2011', 'utc_offset': None, 'time_zone': None, 'geo_enabled': True, 'lang': None, 'contributors_enabled': False, 'is_trans

{'created_at': 'Fri Apr 24 03:08:33 +0000 2020', 'id': 1253521180226699272, 'id_str': '1253521180226699272', 'text': '@WrxChad Based &amp; Blessed🙏🏽', 'display_text_range': [9, 30], 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'truncated': False, 'in_reply_to_status_id': 1253520796154241025, 'in_reply_to_status_id_str': '1253520796154241025', 'in_reply_to_user_id': 84360160, 'in_reply_to_user_id_str': '84360160', 'in_reply_to_screen_name': 'WrxChad', 'user': {'id': 1511638273, 'id_str': '1511638273', 'name': 'TrivTron2020', 'screen_name': 'RyaninCleveland', 'location': 'Cleveland, OH', 'url': 'http://gettrumpybear.com', 'description': 'Nick Sandman Fan Club🇺🇸😏✊🏽', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 376, 'friends_count': 842, 'listed_count': 6, 'favourites_count': 48181, 'statuses_count': 25439, 'created_at': 'Wed Jun 12 20:59:57 +0000 2013', 'utc_offset': None, 'time_zone': None, 'geo_e

{'created_at': 'Fri Apr 24 03:08:33 +0000 2020', 'id': 1253521181182963712, 'id_str': '1253521181182963712', 'text': '@realtimrozon @Jemga @AdriyanRae @AlexPiaraMcG @SYFY Cute https://t.co/ym74Xu7RZ0', 'display_text_range': [53, 57], 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'truncated': False, 'in_reply_to_status_id': 1253520882334662656, 'in_reply_to_status_id_str': '1253520882334662656', 'in_reply_to_user_id': 3793310234, 'in_reply_to_user_id_str': '3793310234', 'in_reply_to_screen_name': 'realtimrozon', 'user': {'id': 23882409, 'id_str': '23882409', 'name': 'LAURA 🦄🌈🦋🌊🔥#EARPNOW', 'screen_name': 'MsLSpatz', 'location': 'Reading, Pa', 'url': 'https://twitter.com/@MsLspatz', 'description': 'Wynonna Earp1-4 + #E4L* EarperFamily * #FIGHTFORWYNONNA * #WayHaught * AmericanHouseWife* #SwerveSeries* StepNotSisters* #FBICBS #LOVEisLOVE #StartTheWave', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 241

{'created_at': 'Fri Apr 24 03:08:33 +0000 2020', 'id': 1253521182399369217, 'id_str': '1253521182399369217', 'text': 'thank god! this game fell off years ago..save the money for nba2k21', 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 2262767612, 'id_str': '2262767612', 'name': 'Daves_thaMan', 'screen_name': 'Dblade919', 'location': 'Laurel, MD', 'url': 'https://www.twitch.tv/dblade919', 'description': 'Left Hawaii🏝🏖 In Maryland🌆 E4👨🏾\u200d💻 USAF', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 47, 'friends_count': 149, 'listed_count': 0, 'favourites_count': 12851, 'statuses_count': 7827, 'created_at': 'Thu Dec 26 12:13:33 +0000 2013', 'utc_offset': None, 'time_zone': None, 'geo_enabled': True, 'lang': None,

...

{'created_at': 'Fri Apr 24 03:09:31 +0000 2020', 'id': 1253521424230289409, 'id_str': '1253521424230289409', 'text': '@Jordanhumess @presidentdajour EW I LOVE YOU', 'display_text_range': [31, 44], 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'truncated': False, 'in_reply_to_status_id': 1253519261097738240, 'in_reply_to_status_id_str': '1253519261097738240', 'in_reply_to_user_id': 3009723062, 'in_reply_to_user_id_str': '3009723062', 'in_reply_to_screen_name': 'Jordanhumess', 'user': {'id': 723297708547694593, 'id_str': '723297708547694593', 'name': 'Isa Mo', 'screen_name': 'isamorales__', 'location': 'United States', 'url': None, 'description': 'tglj💋 | killian | 3x summit champion & 2x nca champion', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 836, 'friends_count': 591, 'listed_count': 1, 'favourites_count': 23560, 'statuses_count': 6563, 'created_at': 'Thu Apr 21 23:49:46 +0000 2016', 'utc_offs

{'created_at': 'Fri Apr 24 03:09:31 +0000 2020', 'id': 1253521425027260417, 'id_str': '1253521425027260417', 'text': 'https://t.co/2dNqCuZmMO', 'display_text_range': [0, 0], 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 896610385, 'id_str': '896610385', 'name': 'Josh Hadden, M.A.', 'screen_name': 'CoachJoshHadden', 'location': 'Aiken County, SC', 'url': None, 'description': 'Georgia born. Carolina raised. Husband. Father. PE Teacher. Golf Coach. Former Football/Softball/Wrestling/Track Coach. Aspiring school administrator.', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 735, 'friends_count': 507, 'listed_count': 6, 'favourites_count': 3286, 'statuses_count': 9679, 'created_at': 'Mon Oct 22 02:47:50 +0000 2

{'created_at': 'Fri Apr 24 03:09:32 +0000 2020', 'id': 1253521426755268608, 'id_str': '1253521426755268608', 'text': "@IanColdwater @0xfraq so Brandi or something seem like a good choice based on hamming distance, but I'm open to suggestions", 'display_text_range': [22, 123], 'source': '<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>', 'truncated': False, 'in_reply_to_status_id': 1253518592907378690, 'in_reply_to_status_id_str': '1253518592907378690', 'in_reply_to_user_id': 711367366756720640, 'in_reply_to_user_id_str': '711367366756720640', 'in_reply_to_screen_name': 'IanColdwater', 'user': {'id': 6651022, 'id_str': '6651022', 'name': 'Brandon Dimcheff | 🐝🔅👨\u200d🍳', 'screen_name': 'bdimcheff', 'location': 'Ann Arbor, MI', 'url': 'http://brandon.dimcheff.com', 'description': 'Happily an Ann Arborite, computer nerd, cat dad, best skier on the mountain, @bdimcheff@a2mi.social. Go Blue. he/him', 'translator_type': 'none', 'protected': False, 'verified

{'created_at': 'Fri Apr 24 03:09:32 +0000 2020', 'id': 1253521427707371520, 'id_str': '1253521427707371520', 'text': 'Sis how you tweet and deleted @Beyonce', 'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', 'truncated': False, 'in_reply_to_status_id': None, 'in_reply_to_status_id_str': None, 'in_reply_to_user_id': None, 'in_reply_to_user_id_str': None, 'in_reply_to_screen_name': None, 'user': {'id': 2940898168, 'id_str': '2940898168', 'name': 'not feeling it', 'screen_name': '711hollywood_', 'location': 'Atlanta, GA', 'url': 'https://www.instagram.com/p/BqgMaajlR2Y/?igshid=rjvn6gtgfvyi', 'description': 'stay out ya feelings ain’t no money there 📸:711hollywood 🐝', 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 631, 'friends_count': 2277, 'listed_count': 2, 'favourites_count': 34575, 'statuses_count': 19270, 'created_at': 'Thu Dec 25 15:50:11 +0000 2014', 'utc_offset': None, 'time_zone': None, 'geo_enab

finished
finished
